# Superheroes NLP analysis

In [15]:
# Superheroes NLP analysis predict creator using history text

In [14]:
#!pip install pandas_profiling

In [56]:
#libraries
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
import nltk
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.corpus import stopwords
import string
import re
nltk.download('stopwords')
stemmer = nltk.SnowballStemmer("english")
import joblib
import warnings

warnings.filterwarnings("ignore")


[nltk_data] Downloading package stopwords to /usr/share/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
#read data
df = pd.read_csv('/kaggle/input/superheroes-nlp-dataset/superheroes_nlp_dataset.csv')
df.head(5)

name               real_name               full_name  \
0        3-D Man     Delroy Garrett, Jr.     Delroy Garrett, Jr.   
1  514A (Gotham)             Bruce Wayne                     NaN   
2         A-Bomb  Richard Milhouse Jones  Richard Milhouse Jones   
3             Aa                      Aa                     NaN   
4     Aaron Cash              Aaron Cash              Aaron Cash   

  overall_score                                       history_text  \
0             6  Delroy Garrett, Jr. grew up to become a track ...   
1            10  He was one of the many prisoners of Indian Hil...   
2            20   Richard "Rick" Jones was orphaned at a young ...   
3            12  Aa is one of the more passive members of the P...   
4             5  Aaron Cash is the head of security at Arkham A...   

                                         powers_text  intelligence_score  \
0                                                NaN                  85   
1                                                NaN                 100   
2    On rare occasions, and through unusual circu...                  80   
3                                                NaN                  80   
4                                                NaN                  80   

   strength_score  speed_score  durability_score  ...  has_flight  \
0              30           60                60  ...         0.0   
1              20           30                50  ...         0.0   
2             100           80               100  ...         0.0   
3              50           55                45  ...         0.0   
4              10           25                40  ...         0.0   

   has_accelerated_healing has_weapons_master has_intelligence has_reflexes  \
0                      0.0                0.0              0.0          0.0   
1                      0.0                0.0              0.0          1.0   
2                      1.0                0.0              0.0          1.0   
3                      0.0                0.0              0.0          0.0   
4                      0.0                1.0              0.0          0.0   

  has_super_speed has_durability has_stamina has_agility has_super_strength  
0             1.0            0.0         0.0         0.0                1.0  
1             0.0            1.0         0.0         0.0                1.0  
2             1.0            1.0         1.0         1.0                1.0  
3             0.0            0.0         0.0         0.0                0.0  
4             0.0            0.0         0.0         0.0                0.0  

[5 rows x 81 columns]

In [6]:
#EDA

In [8]:
from pandas_profiling import ProfileReport

In [9]:
profile = ProfileReport(df, title='Pandas Profiling Report', explorative=True)
# save report 
profile.to_file("output_report.html")
# display report 
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [11]:
df.head()

name               real_name               full_name  \
0        3-D Man     Delroy Garrett, Jr.     Delroy Garrett, Jr.   
1  514A (Gotham)             Bruce Wayne                     NaN   
2         A-Bomb  Richard Milhouse Jones  Richard Milhouse Jones   
3             Aa                      Aa                     NaN   
4     Aaron Cash              Aaron Cash              Aaron Cash   

  overall_score                                       history_text  \
0             6  Delroy Garrett, Jr. grew up to become a track ...   
1            10  He was one of the many prisoners of Indian Hil...   
2            20   Richard "Rick" Jones was orphaned at a young ...   
3            12  Aa is one of the more passive members of the P...   
4             5  Aaron Cash is the head of security at Arkham A...   

                                         powers_text  intelligence_score  \
0                                                NaN                  85   
1                                                NaN                 100   
2    On rare occasions, and through unusual circu...                  80   
3                                                NaN                  80   
4                                                NaN                  80   

   strength_score  speed_score  durability_score  ...  has_flight  \
0              30           60                60  ...         0.0   
1              20           30                50  ...         0.0   
2             100           80               100  ...         0.0   
3              50           55                45  ...         0.0   
4              10           25                40  ...         0.0   

   has_accelerated_healing has_weapons_master has_intelligence has_reflexes  \
0                      0.0                0.0              0.0          0.0   
1                      0.0                0.0              0.0          1.0   
2                      1.0                0.0              0.0          1.0   
3                      0.0                0.0              0.0          0.0   
4                      0.0                1.0              0.0          0.0   

  has_super_speed has_durability has_stamina has_agility has_super_strength  
0             1.0            0.0         0.0         0.0                1.0  
1             0.0            1.0         0.0         0.0                1.0  
2             1.0            1.0         1.0         1.0                1.0  
3             0.0            0.0         0.0         0.0                0.0  
4             0.0            0.0         0.0         0.0                0.0  

[5 rows x 81 columns]

In [12]:
df.columns

Index(['name', 'real_name', 'full_name', 'overall_score', 'history_text',
       'powers_text', 'intelligence_score', 'strength_score', 'speed_score',
       'durability_score', 'power_score', 'combat_score', 'superpowers',
       'alter_egos', 'aliases', 'place_of_birth', 'first_appearance',
       'creator', 'alignment', 'occupation', 'base', 'teams', 'relatives',
       'gender', 'type_race', 'height', 'weight', 'eye_color', 'hair_color',
       'skin_color', 'img', 'has_electrokinesis', 'has_energy_constructs',
       'has_mind_control_resistance', 'has_matter_manipulation',
       'has_telepathy_resistance', 'has_mind_control', 'has_enhanced_hearing',
       'has_dimensional_travel', 'has_element_control', 'has_size_changing',
       'has_fire_resistance', 'has_fire_control', 'has_dexterity',
       'has_reality_warping', 'has_illusions', 'has_energy_beams',
       'has_peak_human_condition', 'has_shapeshifting', 'has_heat_resistance',
       'has_jump', 'has_self-sustenance', 'ha

In [13]:
#take creator and history text

In [30]:
df=df[["history_text","creator"]]

In [17]:
#preprocesing

In [31]:
#remove number vs
df['history_text'] = df['history_text'].str.lower().replace('[^\w\s]', '', regex=True).replace('\d+', '', regex=True).replace('\n', '', regex=True).replace('\r', '', regex=True)
df.head(5)

history_text        creator
0  delroy garrett jr grew up to become a track st...  Marvel Comics
1  he was one of the many prisoners of indian hil...      DC Comics
2   richard rick jones was orphaned at a young ag...  Marvel Comics
3  aa is one of the more passive members of the p...      DC Comics
4  aaron cash is the head of security at arkham a...      DC Comics

In [32]:
df["creator"].unique()

array(['Marvel Comics', 'DC Comics', 'George Lucas', 'Dark Horse Comics',
       nan, 'Blizzard Entertainment', 'NBC - Heroes', 'Lego', 'Wildstorm',
       'Ubisoft', 'J. R. R. Tolkien', 'Image Comics',
       'George R. R. Martin', 'Capcom', 'Icon Comics', 'SyFy',
       'Hanna-Barbera', 'Hasbro', 'Clive Barker', 'Team Epic TV',
       'South Park', 'Shueisha', 'Namco', 'HarperCollins', 'ABC Studios',
       'Universal Studios', 'Star Trek', 'J. K. Rowling', 'Konami',
       'Sony Pictures', 'Stephen King', 'Dreamworks', 'Disney',
       'Ian Fleming', 'Nintendo', 'Microsoft', 'Cartoon Network',
       'Mortal Kombat', 'IDW Publishing', 'Mattel', 'Sega',
       'Matt Groening'], dtype=object)

In [42]:
#fill mising values with mean
df["creator"].fillna(df["creator"].mode()[0], inplace=True)

In [43]:
df.isnull().sum()

history_text    90
creator          0
dtype: int64

In [46]:
#drop mising values
df.dropna(inplace=True)

In [47]:
df.reset_index(drop=True,inplace=True)

In [51]:
# x y split
x=df["history_text"]
y=df[["creator"]]

In [65]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB

# Vectorizing text data
vect = CountVectorizer(ngram_range=(1, 2), stop_words="english")
x = vect.fit_transform(df['history_text'])  # Make sure to replace 'your_dataframe' with the actual variable name

# Categorical columns
y_encoded = df.drop('history_text', axis=1)

# Train-test split
x_train, x_test, y_train, y_test = train_test_split(x, y_encoded, test_size=0.20, random_state=42)

# Modeling
nb = MultinomialNB()
model = nb.fit(x_train, y_train)
pred = nb.predict(x_test)


In [66]:
accuracy_score(pred,y_test)

0.7610294117647058

In [67]:
#save model
joblib.dump(model,"model.joblib")

['model.joblib']

In [68]:
#sources

-Zafer Acar Notes ,-[https://chat.openai.com/]